In [1]:
import matplotlib.pyplot as plt
import numpy as np
import sympy
from src.v2.impl.conditions import StepCountCondition, PrecisionCondition, AbsolutePrecisionCondition
from src.v2.impl.methods import CoordinateDescent, GoldenRatioMethod
from src.v2.impl.metrics import StepCount, CallCount, GradientCallCount, HessianCallCount, PrecisionCount, \
    AbsolutePrecisionCount, AbsolutePrecision, MinAbsolutePrecision
from src.v2.impl.oraculs import LambdaOracul, SymbolOracul
from src.v2.runner.debug import FULL_DEBUG
from src.v2.runner.runner import Runner, FULL_VISUALIZE, NO_VISUALIZE
from src.v2.visualization.animation import Animator, FULL_ANIMATION
from src.v2.runner.runner import TABLE
from src.v2.impl.methods import GradientDescent, ScipyMethod, Newton, NewtonBase
from IPython.display import display, HTML

In [2]:
from sympy import diff, symbols

diff(symbols('x y'), symbols('x')) == diff(symbols('y x'), symbols('x'))

False

In [3]:
x, y, z = symbols('x y z')
expr = x**3 + 4*x*y - z
type(expr)

sympy.core.add.Add

In [4]:
from src.common import Point
from src.common.oracul import SymbolOracul, GradientLambdaOracul

x, y, z  = symbols('x y z')
expr = x * 0.26 * (x ** 2 + y ** 2) - 0.48 * x * y 
test = SymbolOracul(expr, ['x', 'y'])
base_differential = GradientLambdaOracul(lambda x, y: 0.26 * (x ** 2 + y ** 2) - 0.48 * x * y,
                                         lambda x, y: np.array([0.52 * x - 0.48 * y, 0.52 * y - 0.48 * x],
                                                               dtype=np.float64))

In [5]:
test.evaluate_hessian(Point(np.array([1, 2, 3])))

array([[1.56, 0.56],
       [0.56, 0.52]])

In [6]:
from src.v2.impl.methods import Wolfe
#self.c1 = params["c1"]
#        self.c2 = params["c2"]
 #       self.eps = params["aprox_dec"]
  #      self.max_iters = params["max_iters"]
wolfe = Wolfe(c1=0.1, c2=0.2, aprox_dec=1e-11, max_iters=20)

In [9]:

from src.v2.impl.oraculs import LambdaOracul
#bad_defined_absolute = SymbolOracul(1000 * (x - 100) ** 10 + 100 * (y + 20) ** 10, ['x', 'y'])
bad_defined = LambdaOracul(lambda x, y: 1000 * (np.float64(x) - 100) ** 10 + 100 * (np.float64(y) + 20) ** 10)
min_point = np.array([100, -20])
metrics = [StepCount(), CallCount(), GradientCallCount(), HessianCallCount(),
           AbsolutePrecisionCount(0.001, min_point),
           MinAbsolutePrecision(min_point)]
conditions = [StepCountCondition(1000), PrecisionCondition(0.00001)]
#AbsolutePrecisionCondition(0.0001, min_point)            
animations = [Animator()]

modules = animations + metrics + conditions
methods2 = [
    Newton(method=wolfe, aprox_dec=1e-14)
]
oraculs = [bad_defined]
point = np.array([-100, -200])
result = Runner.run(methods2, oraculs, point, modules, precision=1e-5, **TABLE, **NO_VISUALIZE)

KeyboardInterrupt: 

In [10]:
from src.v2.impl.oraculs import LambdaOracul
wolfe = Wolfe(c1=0.1, c2=0.2, aprox_dec=1e-7, max_iters=3)
rosenbrok = LambdaOracul(lambda x, y: (1 - x)**2 + 100 * (y - x**2)**2)
#bad_defined_absolute = SymbolOracul(1000 * (x - 100) ** 10 + 100 * (y + 20) ** 10, ['x', 'y'])
bad_defined = LambdaOracul(lambda x, y: 1000 * (np.float64(x) - 100) ** 10 + 100 * (np.float64(y) + 20) ** 10)
min_point = np.array([100, -20])
metrics = [StepCount(), CallCount(), GradientCallCount(), HessianCallCount(),
           AbsolutePrecisionCount(0.001, min_point),
           MinAbsolutePrecision(min_point)]
conditions = [StepCountCondition(1000), PrecisionCondition(0.00001)]
#AbsolutePrecisionCondition(0.0001, min_point)            
animations = [Animator()]

modules = animations + metrics + conditions
methods2 = [
    Newton(method=wolfe, aprox_dec=1e-7, learning_rate=0.5)
]
oraculs = [rosenbrok]
point = np.array([-100, -200])
result = Runner.run(methods2, oraculs, point, modules, precision=1e-5, **TABLE, **NO_VISUALIZE, **FULL_DEBUG)

[DEBUG][Metric][MinAbsolutePrecision] Prepared oracul
[DEBUG][Oracul] Added debug to oracul
[DEBUG][Method][Newton(0.5,Wolfe(0.1,0.2,eps=1e-07),eps=1e-07)] Initial state is NewtonState(point=array([-100, -200]), eps=inf, index=1, prev_point=None)
[DEBUG][Metric][MinAbsolutePrecision][1] 269.0724809414742
[DEBUG][Oracul][Hessian] Evaluated at [-100 -200] - [[1.2080002e+07 4.0000000e+04]
 [4.0000000e+04 2.0000000e+02]]
[DEBUG][Oracul][Gradient] Evaluated at [-100 -200] - [-4.08000202e+08 -2.04000000e+06]
[DEBUG][Oracul][Value] Evaluated at [ -99.99995048 9999.99009632] - 10200.989997755436
[DEBUG][Oracul][Value] Evaluated at [ -99.99995048 9999.99009632] - 10200.989997755436
[DEBUG][Oracul][Value] Evaluated at [  -99.99985145 30399.97028897] - 41616010195.242485
[DEBUG][Oracul][Value] Evaluated at [  -100.00004952 -10399.99009632] - 41616010199.14084
[DEBUG][Oracul][Value] Evaluated at [  -99.99990097 20199.98019265] - 10404010199.080826
[DEBUG][Oracul][Value] Evaluated at [-100. -200.] 

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



[DEBUG][Oracul][Value] Evaluated at [-100. -200.] - 10404010201.0
[DEBUG][Oracul][Value] Evaluated at [-100. -200.] - 10404010201.0
[DEBUG][Oracul][Value] Evaluated at [  -99.99990097 20199.98019265] - 10404010199.080826
[DEBUG][Oracul][Value] Evaluated at [  -100.00009903 -20599.98019265] - 93636010195.44255
[DEBUG][Oracul][Value] Evaluated at [ -99.99995048 9999.99009632] - 10200.989997755436
[DEBUG][Oracul][Value] Evaluated at [  -100.00004952 -10399.99009632] - 41616010199.14084
[DEBUG][Oracul][Value] Evaluated at [ -99.99997524 4899.99504816] - 2601010201.2305202
[DEBUG][Oracul][Value] Evaluated at [ -100.00002476 -5299.99504816] - 23409010200.30219
[DEBUG][Oracul][Value] Evaluated at [ -99.99998762 2349.99752408] - 5852260201.173906
[DEBUG][Oracul][Value] Evaluated at [ -100.00001238 -2749.99752408] - 16256260200.709272
[DEBUG][Oracul][Value] Evaluated at [ -99.99999381 1074.99876204] - 7965572701.101585
[DEBUG][Oracul][Value] Evaluated at [ -100.00000619 -1474.99876204] - 131675

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



KeyboardInterrupt: 